# Nemo for speaker recognition 
find nemo here - https://docs.nvidia.com/deeplearning/nemo/user-guide/docs/en/stable/index.html

tryin nemo by nvidia to predict the speech transcription. Nemo has pretrained models and is easy to transfer learn things. in this notebook I am trying to use nemo for predict the speech transcription from wolof to french mostly nemo has good performance In asr.

- first training
**train stt_fr_quartznet15_5.nemo from [Fork of prep files before major training on 00_asr](https://www.kaggle.com/tricia1/fork-of-prep-files-before-major-training-on-00-asr) version 1 .loss of 0.16221396988406 on zindi public LB**

- second training

**retrain model trained_model2_v9 from [Fork of prep files before major training on 00_asr](https://www.kaggle.com/tricia1/fork-of-prep-files-before-major-training-on-00-asr) version 1 .loss of 0.0.160862443789273 on zindi public LB**

- third training

**re retrain model forkretrained_model10_v1.nemo  from [10_1 re_retrain fork prepfilesbeforemajortraining](https://www.kaggle.com/francsearl/10-retrain-fork-prepfilesbeforemajortraining/notebook) version 2 .loss of 0.129138081288274 on zindi public LB**

current fourth training

**re re retrain model forkretrained_model11_v1.nemo from [10-1-1-reretrain-fork-prepfilesbeforemajortraining](https://www.kaggle.com/troublem1/10-1-re-retrain-fork-prepfilesbeforemajortraining/notebook) version 1**

In [1]:
import os
import pandas as pd
import numpy as np
from pathlib import Path
import torch
import pytorch_lightning as pl
from pytorch_lightning.loggers.tensorboard import TensorBoardLogger
import librosa
from tqdm.notebook import tqdm
import warnings
warnings.filterwarnings('ignore')

/opt/conda/lib/python3.7/site-packages/torchaudio/backend/utils.py:54: UserWarning: "sox" backend is being deprecated. The default backend will be changed to "sox_io" backend in 0.8.0 and "sox" backend will be removed in 0.9.0. Please migrate to "sox_io" backend. Please refer to https://github.com/pytorch/audio/issues/903 for the detail.
  '"sox" backend is being deprecated. '


In [3]:
train = pd.read_csv('../input/bamtu-final/files/sythe_noise/files/sn_train.csv')
train['transcription'] = list([i.lower().replace('œ' , 'oe').replace('-',"").replace(',' ,' ').replace('(' , ' ').replace(')' , ' ').replace('"' , "'").replace('"' , "'").replace("'" , "'").replace("'" , "'").replace("’" , "'").strip(' ') for i in train['transcription'].values ])

In [4]:
# wolof complete characters retrieved from wikipedia
print(set(list(set('A À B C D E É Ë F G I J K L M N Ñ Ŋ O Ó P Q R S T U W X Y'.lower().split(' ')))))

{'ó', 'c', 'f', 'b', 'a', 'k', 'r', 'g', 'u', 'à', 'i', 't', 'l', 'ë', 'y', 'd', 'n', 'q', 'ñ', 'w', 'p', 'ŋ', 's', 'é', 'j', 'o', 'e', 'm', 'x'}


In [5]:
# generate unit words or syllables from transcriptions
wordvocab = sorted(list(set([v.lower().strip(' ') 
                                 for i in train['transcription'].values for v in i.split(' ')])))


# #retrive unique character by character strings
charvocab = [v for i in wordvocab for v in i]

print('french: ', set(list(set(vocab1))) ) 
# diff between wolof and french/latin
set(list(set(charvocab))) - set('A À B C D E É Ë F G I J K L M N Ñ Ŋ O Ó P Q R S T U W X Y'.lower().split(' '))

french:  {'c', 'è', 'h', 'f', 'b', 'a', 'î', 'k', 'v', 'r', 'g', 'u', 'z', 'i', 't', 'l', 'â', 'ë', 'y', 'd', 'n', 'q', 'w', "'", 'p', 'o', 'ç', 's', 'é', 'j', 'ô', 'e', 'm', 'x'}


{"'", 'h', 'v', 'z', 'â', 'ç', 'è', 'î', 'ô'}

In [21]:
import os
# # setup nemo
# BRANCH = 'r1.0.0b3'
# !python -m pip install git+https://github.com/NVIDIA/NeMo.git@$BRANCH#egg=nemo_toolkit[asr]
# NEMO_ROOT = os.getcwd()
#or 
! pip install nemo['asr']==1.0.0b3

  Cloning https://github.com/NVIDIA/NeMo.git (to revision r1.0.0b3) to /tmp/pip-install-c8qpc24b/nemo-toolkit_e389f3dd1aa24f1e98f1d5828551f4de
  Running command git clone -q https://github.com/NVIDIA/NeMo.git /tmp/pip-install-c8qpc24b/nemo-toolkit_e389f3dd1aa24f1e98f1d5828551f4de
  Running command git checkout -b r1.0.0b3 --track origin/r1.0.0b3
  Switched to a new branch 'r1.0.0b3'
  Branch 'r1.0.0b3' set up to track remote branch 'r1.0.0b3' from 'origin'.
     |████████████████████████████████| 561 kB 4.5 MB/s 
     |████████████████████████████████| 101 kB 9.4 MB/s 
     |████████████████████████████████| 123 kB 56.2 MB/s 
     |████████████████████████████████| 1.3 MB 52.0 MB/s 
     |████████████████████████████████| 179 kB 45.3 MB/s 
     |████████████████████████████████| 47 kB 3.5 MB/s 
     |████████████████████████████████| 3.1 MB 46.1 MB/s 
     |████████████████████████████████| 112 kB 60.8 MB/s 
     |████████████████████████████████| 1.1 MB 48.4 MB/s 
     |██████████████

In [22]:
import nemo
# NeMo's ASR collection - this collections contains complete ASR models and
# building blocks (modules) for ASR
import nemo.collections.asr as nemo_asr
from omegaconf import OmegaConf

[NeMo W 2021-05-21 10:04:51 experimental:28] Module <class 'nemo.collections.asr.data.audio_to_text.AudioToCharDataset'> is experimental, not ready for production and is not fully supported. Use at your own risk.
[NeMo W 2021-05-21 10:04:51 experimental:28] Module <class 'nemo.collections.asr.data.audio_to_text.AudioToBPEDataset'> is experimental, not ready for production and is not fully supported. Use at your own risk.
[NeMo W 2021-05-21 10:04:51 experimental:28] Module <class 'nemo.collections.asr.data.audio_to_text.AudioLabelDataset'> is experimental, not ready for production and is not fully supported. Use at your own risk.
[NeMo W 2021-05-21 10:04:51 experimental:28] Module <class 'nemo.collections.asr.data.audio_to_text._TarredAudioToTextDataset'> is experimental, not ready for production and is not fully supported. Use at your own risk.
[NeMo W 2021-05-21 10:04:51 experimental:28] Module <class 'nemo.collections.asr.data.audio_to_text.TarredAudioToCharDataset'> is experimental,

[nltk_data] Downloading package averaged_perceptron_tagger to
[nltk_data]     /usr/share/nltk_data...
[nltk_data]   Package averaged_perceptron_tagger is already up-to-
[nltk_data]       date!
[nltk_data] Downloading package cmudict to /usr/share/nltk_data...
[nltk_data]   Package cmudict is already up-to-date!


[NeMo W 2021-05-21 10:04:56 experimental:28] Module <class 'nemo.collections.asr.losses.ctc.CTCLoss'> is experimental, not ready for production and is not fully supported. Use at your own risk.
[NeMo W 2021-05-21 10:04:56 experimental:28] Module <class 'nemo.collections.asr.data.audio_to_text_dali.AudioToCharDALIDataset'> is experimental, not ready for production and is not fully supported. Use at your own risk.


In [23]:
nemo_asr.models.EncDecCTCModel.list_available_models()

[PretrainedModelInfo(pretrained_model_name='QuartzNet15x5Base-En', description='QuartzNet15x5 model trained on six datasets: LibriSpeech, Mozilla Common Voice (validated clips from en_1488h_2019-12-10), WSJ, Fisher, Switchboard, and NSC Singapore English. It was trained with Apex/Amp optimization level O1 for 600 epochs. The model achieves a WER of 3.79% on LibriSpeech dev-clean, and a WER of 10.05% on dev-other.', location='https://api.ngc.nvidia.com/v2/models/nvidia/nemospeechmodels/versions/1.0.0a5/files/QuartzNet15x5Base-En.nemo', class_=None),
 PretrainedModelInfo(pretrained_model_name='QuartzNet15x5Base-Zh', description='QuartzNet15x5 model trained on ai-shell2 Mandarin Chinese dataset.', location='https://api.ngc.nvidia.com/v2/models/nvidia/nemospeechmodels/versions/1.0.0a5/files/QuartzNet15x5Base-Zh.nemo', class_=None),
 PretrainedModelInfo(pretrained_model_name='QuartzNet5x5LS-En', description='QuartzNet5x5 model trained on LibriSpeech dataset only. The model achieves a WER of

In [26]:
# This line will download pre-trained QuartzNet15x5 model from NVIDIA's NGC cloud and instantiate it for you
quartznet_15x5 = nemo_asr.models.EncDecCTCModel.restore_from("./forkretrained_model111_v1.nemo")#"./stt_fr_quartznet15x5.nemo")
ll = "../input/bamtu-final/files/sythe_noise/audios/train/0031672b4484f963c8a07babe6f713dd559539d44140e80ac19708db36d9712d81dd5b170c016f65bbd6763372c35bfc984a55448e356f3161dbf8d7c28aa047.wav"#'../input/bamtu-asr-1/interim_files/files/convertedwavs/002e50c29ac2890c7cb3b3d63dcbe512bc6850de206ca80477704628fb1194de25fb31484fd3ef7ec27efbe87524a8d325c9e7e08d5b1e9f2b0ca2a19fe12089.wav'
ll2 = "../input/bamtu-final/files/sythe_noise/audios/train/004bb970ff5217dc663cd9d69cf6dccc8b4197062ad48d698abc13661dc455d62f5a052a3e9812bfc2e97b6eb800fc28ecbab8f5e09187ebd1d9ce6c94c27a59.wav"#'../input/bamtu-asr-1/interim_files/files/convertedwavs/0031672b4484f963c8a07babe6f713dd559539d44140e80ac19708db36d9712d81dd5b170c016f65bbd6763372c35bfc984a55448e356f3161dbf8d7c28aa047.wav'

files = [ll,ll2]
for fname, transcription in zip(files, quartznet_15x5.transcribe(paths2audio_files=files)):
    print(f"Audio in {fname} was recognized as: {transcription}")

[NeMo W 2021-05-21 10:05:00 modelPT:110] Please call the ModelPT.setup_training_data() method and provide a valid configuration file to setup the train data loader.
    Train config : 
    manifest_filepath: ../input/bamtu-full-json/sn json/train_manifest.json
    sample_rate: 16000
    labels:
    - ' '
    - a
    - b
    - c
    - d
    - e
    - f
    - g
    - h
    - i
    - j
    - k
    - l
    - m
    - 'n'
    - o
    - p
    - q
    - r
    - s
    - t
    - u
    - v
    - w
    - x
    - 'y'
    - z
    - ''''
    - ç
    - é
    - â
    - ê
    - î
    - ô
    - û
    - à
    - è
    - ù
    - ë
    - ï
    - ü
    - ÿ
    batch_size: 50
    trim_silence: true
    max_duration: 16.7
    shuffle: true
    is_tarred: false
    tarred_audio_filepaths: null
    tarred_shard_strategy: scatter
    
[NeMo W 2021-05-21 10:05:00 modelPT:117] Please call the ModelPT.setup_validation_data() or ModelPT.setup_multiple_validation_data() method and provide a valid configuration file to 

[NeMo I 2021-05-21 10:05:00 features:241] PADDING: 16
[NeMo I 2021-05-21 10:05:00 features:258] STFT using torch
[NeMo I 2021-05-21 10:05:06 modelPT:257] Model EncDecCTCModel was successfully restored from ../input/10-1-1-reretrain-fork-prepfilesbeforemajortraining/forkretrained_model111_v1.nemo.
Audio in ../input/bamtu-full-dataset/files/sythe_no_noise/audios/train/0031672b4484f963c8a07babe6f713dd559539d44140e80ac19708db36d9712d81dd5b170c016f65bbd6763372c35bfc984a55448e356f3161dbf8d7c28aa047.wav was recognized as: ecole elementaire pikine nord
Audio in ../input/bamtu-full-dataset/files/sythe_no_noise/audios/train/004bb970ff5217dc663cd9d69cf6dccc8b4197062ad48d698abc13661dc455d62f5a052a3e9812bfc2e97b6eb800fc28ecbab8f5e09187ebd1d9ce6c94c27a59.wav was recognized as: ouakam


In [27]:
quartznet_15x5.cfg['validation_ds'] ['labels']

[' ', 'a', 'b', 'c', 'd', 'e', 'f', 'g', 'h', 'i', 'j', 'k', 'l', 'm', 'n', 'o', 'p', 'q', 'r', 's', 't', 'u', 'v', 'w', 'x', 'y', 'z', "'", 'ç', 'é', 'â', 'ê', 'î', 'ô', 'û', 'à', 'è', 'ù', 'ë', 'ï', 'ü', 'ÿ']

In [29]:
# --- Config Information ---#

try:
    from ruamel.yaml import YAML
except ModuleNotFoundError:
    from ruamel_yaml import YAML
config_path = "../input/bamtu-jsonfinal/10_1_1_5wo_quartznet15x5r1.0.0b3/stt_wo_quartznet15x5.yaml" 

yaml = YAML(typ='safe')
with open(config_path) as f:
    params = yaml.load(f)
print(params)

{'name': 'QuartzNet15x5', 'model': {'sample_rate': 16000, 'repeat': 5, 'dropout': 0.0, 'separable': True, 'labels': [' ', 'a', 'b', 'c', 'd', 'e', 'f', 'g', 'h', 'i', 'j', 'k', 'l', 'm', 'n', 'o', 'p', 'q', 'r', 's', 't', 'u', 'v', 'w', 'x', 'y', 'z', "'"], 'train_ds': {'manifest_filepath': '???', 'sample_rate': 16000, 'labels': [' ', 'a', 'b', 'c', 'd', 'e', 'f', 'g', 'h', 'i', 'j', 'k', 'l', 'm', 'n', 'o', 'p', 'q', 'r', 's', 't', 'u', 'v', 'w', 'x', 'y', 'z', "'"], 'batch_size': 32, 'trim_silence': True, 'max_duration': 16.7, 'shuffle': True, 'is_tarred': False, 'tarred_audio_filepaths': None, 'tarred_shard_strategy': 'scatter'}, 'validation_ds': {'manifest_filepath': '???', 'sample_rate': 16000, 'labels': [' ', 'a', 'b', 'c', 'd', 'e', 'f', 'g', 'h', 'i', 'j', 'k', 'l', 'm', 'n', 'o', 'p', 'q', 'r', 's', 't', 'u', 'v', 'w', 'x', 'y', 'z', "'"], 'batch_size': 32, 'shuffle': False}, 'test_ds': {'manifest_filepath': None, 'sample_rate': 16000, 'labels': [' ', 'a', 'b', 'c', 'd', 'e', 

In [30]:
params.keys()

dict_keys(['name', 'model', 'trainer', 'exp_manager', 'hydra'])

In [34]:
# setup manifest
train_manifest = '../input/bamtu-full-json/sn json/train_manifest.json' #'train_manifest.json'
validation_manifest = "../input/bamtu-full-json/sn json/test_manifest.json" #'test_manifest.json'
test_manifest = "../input/bamtu-full-json/sn json/test_manifest.json" #'test_manifest.json'

In [35]:
# config.model.train_ds.manifest_filepath = train_manifest
# config.model.validation_ds.manifest_filepath = validation_manifest
# config.model.test_ds.manifest_filepath = validation_manifest

In [36]:
import torch
import pytorch_lightning as pl
from pytorch_lightning.loggers.tensorboard import TensorBoardLogger

In [39]:
params['model']['train_ds']['manifest_filepath'] = train_manifest
params['model']['validation_ds']['manifest_filepath'] = test_manifest
params["exp_manager"]['create_tensorboard_logger'] = False

In [40]:
# Check what kind of vocabulary/alphabet the model has right now
print(quartznet_15x5.decoder.vocabulary)

[' ', 'a', 'b', 'c', 'd', 'e', 'f', 'g', 'h', 'i', 'j', 'k', 'l', 'm', 'n', 'o', 'p', 'q', 'r', 's', 't', 'u', 'v', 'w', 'x', 'y', 'z', "'", 'ç', 'é', 'â', 'ê', 'î', 'ô', 'û', 'à', 'è', 'ù', 'ë', 'ï', 'ü', 'ÿ']


In [42]:
params['model']['optim']

{'name': 'novograd',
 'lr': 0.01,
 'betas': [0.8, 0.5],
 'weight_decay': 0.001,
 'sched': {'name': 'CosineAnnealing',
  'warmup_steps': None,
  'warmup_ratio': None,
  'min_lr': 0.0,
  'last_epoch': -1}}

In [43]:
quartznet_15x5.cfg['optim']  

{'name': 'novograd', 'lr': 0.00010647819614318494, 'betas': [0.8, 0.5], 'weight_decay': 0.001, 'sched': {'name': 'CosineAnnealing', 'warmup_steps': None, 'warmup_ratio': None, 'min_lr': 0.0, 'last_epoch': -1}}

In [44]:
%%time
import copy
from omegaconf import DictConfig

new_opt = copy.deepcopy(params['model']['optim'])

# # Use the smaller learning rate we set before
quartznet_15x5.setup_optimization(optim_config= DictConfig(new_opt))

# # Point to the data we'll use for fine-tuning as the training set
quartznet_15x5.setup_training_data(train_data_config=params['model']['train_ds'])

# # Point to the new validation data for fine-tuning
quartznet_15x5.setup_validation_data(val_data_config=params['model']['validation_ds'])

# # And now we can create a PyTorch Lightning trainer and call `fit` again.
trainer = pl.Trainer(**params['trainer'])
trainer.fit(quartznet_15x5)

[NeMo I 2021-05-21 10:05:10 modelPT:597] Optimizer config = Novograd (
    Parameter Group 0
        amsgrad: False
        betas: [0.8, 0.5]
        eps: 1e-08
        grad_averaging: False
        lr: 0.0001
        weight_decay: 0.001
    )


[NeMo W 2021-05-21 10:05:10 lr_scheduler:542] Neither `max_steps` nor `iters_per_batch` were provided to `optim.sched`, cannot compute effective `max_steps` !
    Scheduler will not be instantiated !


[NeMo I 2021-05-21 10:05:11 collections:173] Dataset loaded with 37193 files totalling 32.57 hours
[NeMo I 2021-05-21 10:05:11 collections:174] 0 files were filtered totalling 0.00 hours
[NeMo I 2021-05-21 10:05:12 collections:173] Dataset loaded with 6564 files totalling 5.74 hours
[NeMo I 2021-05-21 10:05:12 collections:174] 0 files were filtered totalling 0.00 hours


GPU available: True, used: True
TPU available: False, using: 0 TPU cores
LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0]
Using native 16bit precision.
initializing ddp: GLOBAL_RANK: 0, MEMBER: 1/1


[NeMo I 2021-05-21 10:05:12 modelPT:597] Optimizer config = Novograd (
    Parameter Group 0
        amsgrad: False
        betas: [0.8, 0.5]
        eps: 1e-08
        grad_averaging: False
        lr: 0.0001
        weight_decay: 0.001
    )


...

Validating: 0it [00:00, ?it/s]

[NeMo I 2021-05-21 17:38:21 wer:159] 
    
[NeMo I 2021-05-21 17:38:21 wer:160] reference:terminus cap manuel
[NeMo I 2021-05-21 17:38:21 wer:161] decoded  :terminus cap manuel
[NeMo I 2021-05-21 17:38:21 wer:159] 
    
[NeMo I 2021-05-21 17:38:21 wer:160] reference:menuserie ebéniste lamp fall
[NeMo I 2021-05-21 17:38:22 wer:161] decoded  :menuserie ebéniste lamp fall
[NeMo I 2021-05-21 17:38:22 wer:159] 
    
[NeMo I 2021-05-21 17:38:22 wer:160] reference:tally bou bess parcelle
[NeMo I 2021-05-21 17:38:22 wer:161] decoded  :tally bou bess parcelle
[NeMo I 2021-05-21 17:38:22 wer:159] 
    
[NeMo I 2021-05-21 17:38:22 wer:160] reference:terrain mbedou fass
[NeMo I 2021-05-21 17:38:22 wer:161] decoded  :terrain mbedou fass
[NeMo I 2021-05-21 17:38:23 wer:159] 
    
[NeMo I 2021-05-21 17:38:23 wer:160] reference:cinéma poste thiaroye
[NeMo I 2021-05-21 17:38:23 wer:161] decoded  :cinéma poste thiaroye
[NeMo I 2021-05-21 17:38:23 wer:159] 
    
[NeMo I 2021-05-21 17:38:23 wer:160] refer

Validating: 0it [00:00, ?it/s]

[NeMo I 2021-05-21 17:57:49 wer:159] 
    
[NeMo I 2021-05-21 17:57:49 wer:160] reference:terminus cap manuel
[NeMo I 2021-05-21 17:57:49 wer:161] decoded  :terminus cap manuel
[NeMo I 2021-05-21 17:57:49 wer:159] 
    
[NeMo I 2021-05-21 17:57:49 wer:160] reference:menuserie ebéniste lamp fall
[NeMo I 2021-05-21 17:57:49 wer:161] decoded  :menuserie ebéniste lamp fall
[NeMo I 2021-05-21 17:57:49 wer:159] 
    
[NeMo I 2021-05-21 17:57:49 wer:160] reference:tally bou bess parcelle
[NeMo I 2021-05-21 17:57:49 wer:161] decoded  :tally bou bess parcelle
[NeMo I 2021-05-21 17:57:50 wer:159] 
    
[NeMo I 2021-05-21 17:57:50 wer:160] reference:terrain mbedou fass
[NeMo I 2021-05-21 17:57:50 wer:161] decoded  :terrain mbedou fass
[NeMo I 2021-05-21 17:57:50 wer:159] 
    
[NeMo I 2021-05-21 17:57:50 wer:160] reference:cinéma poste thiaroye
[NeMo I 2021-05-21 17:57:50 wer:161] decoded  :cinéma poste thiaroye
[NeMo I 2021-05-21 17:57:51 wer:159] 
    
[NeMo I 2021-05-21 17:57:51 wer:160] refer

1

In [45]:
quartznet_15x5.save_to('./forkretrained_model1115_v1.nemo')